In [23]:
import math
import matplotlib.pyplot as plt
import numpy as np
import os
import cv2
import dlib
import mediapipe as mp
from mediapipe.tasks import python
from mediapipe.tasks.python import vision
from retinaface.commons.postprocess import rotate_facial_area
from retinaface import RetinaFace

In [24]:
def normal_to_pixel(x, y, w, h, invert = False):
    if invert:
        return list(np.array((x, y)) / np.array((w, h)))
    return list((np.array((x, y)) * np.array((w, h))).astype(int))

In [25]:
def get_angle_from_eyes(left_eye, right_eye, degrees = True):
    if right_eye[1] - left_eye[1] == 0:
        return 0, 1
    
    cos_angle = left_eye.dot(right_eye) / (np.linalg.norm(left_eye, 2) * np.linalg.norm(right_eye, 2))
    
    direction = math.copysign(1, (left_eye[1] - right_eye[1]))

    angle = np.arccos(cos_angle)
    if degrees:
        angle = np.rad2deg(angle)
        
    return angle, direction

In [26]:
def rotate_from_angle(image, center, angle, direction, degrees = True):
    if not degrees:
        angle = np.rad2deg(angle)

    rotation_matrix = cv2.getRotationMatrix2D(center, angle * direction, 1)
    rotated_image = cv2.warpAffine(image, rotation_matrix, image.shape[1::-1], flags = cv2.INTER_LINEAR)
    
    return rotated_image

In [27]:
def get_index_center_face(image_center, face_centers):
    return np.argmin(np.sum(np.abs(np.array(image_center) - np.array(face_centers)), axis = 1))

In [28]:
def get_dlib_faces(image):
    # Instantiate a dlib face detector and shape predictor
    detector = dlib.get_frontal_face_detector()
    shape_predictor = dlib.shape_predictor('./pretrained_models/shape_predictor_5_face_landmarks.dat')
    
    # Get faces from image
    detections = detector(image, 0)
    faces = dlib.full_object_detections()
    for detection in detections:
        faces.append(shape_predictor(image, detection))
        
    chip_details = dlib.get_face_chip_details(faces)
    
    chip_index = 0
    
    if len(chip_details) == 0:
        return -1
        
    if len(chip_details) > 1:
        image_center = tuple(np.array(image.shape[1::-1]) / 2)
        face_centers = [(c.rect.center().x, c.rect.center().y) for c in chip_details]
        chip_index = get_index_center_face(image_center, face_centers)
        
    return chip_details[0]

In [29]:
def dlib_align(image, chip_detail):
    face_center = (chip_detail.rect.center().x, chip_detail.rect.center().y)
    rotated_image = rotate_from_angle(image, face_center, chip_detail.angle, 1, degrees = False)
    
    return rotated_image

In [30]:
def get_dlib_region(chip_detail):
    # Dlib's coordinate system has y = 0 at the top of the image, the opposite of numpy
    # Thus, y_min is the top of the rectangle, while y_max, is the bottom of the rectangle
    x_min = int(np.round(chip_detail.rect.left()))
    x_max = int(np.round(chip_detail.rect.right()))

    y_min = int(np.round(chip_detail.rect.top()))
    y_max = int(np.round(chip_detail.rect.bottom()))
    
    return x_min, x_max, y_min, y_max

In [31]:
def get_retinaface_faces(image):
    faces = RetinaFace.detect_faces(img_path = image)
    
    face_key = 'face_1'
    
    if len(faces.keys()) == 0:
        return -1
    
    if len(faces.keys()) > 1:
        image_center = tuple(np.array(image.shape[1::-1]) / 2)
        face_noses = [(faces[key]['landmarks']['nose'][0], faces[key]['landmarks']['nose'][1]) for key in faces.keys()]
        face_index = get_index_center_face(image_center, face_noses)
        face_key = list(faces.keys())[face_index]
    
    return faces[face_key]

In [32]:
def retinaface_align(image, face_data):
    right_eye = np.array(face_data['landmarks']['right_eye'])
    left_eye = np.array(face_data['landmarks']['left_eye'])

    angle, direction = get_angle_from_eyes(left_eye, right_eye)
    
    rotated_image = rotate_from_angle(image, tuple(np.array(image.shape[1::-1]) / 2), angle, direction)

    return rotated_image

In [33]:
def get_retinaface_region(face_data):
    
    x_min, y_min, x_max, y_max = face_data['facial_area']
    
    return x_min, x_max, y_min, y_max

In [59]:
def get_mediapipe_faces(image):
    mp_face_mesh = mp.solutions.face_mesh

    with mp_face_mesh.FaceMesh(static_image_mode = True,
                               max_num_faces = 5,
                               refine_landmarks = True) as face_mesh:
        results = face_mesh.process(image[:,:,::-1])
    
    results_key = 0
    
    if results.multi_face_landmarks is None:
        return -1
    
    if len(results.multi_face_landmarks) > 1:
        image_center = tuple(np.array(image.shape[1::-1]) / 2)
        rough_face_centers = [np.sum((np.array((face.landmark[475].x, face.landmark[475].y)),
                                      np.array((face.landmark[470].x, face.landmark[470].y))), axis = 1) / 2\
                             for face in results.multi_face_landmarks]
        rough_face_centers_norm = [normal_to_pixel(f[0], f[1], image.shape[1], image.shape[0]) for f in rough_face_centers]
        results_key = get_index_center_face(image_center, rough_face_centers_norm)
            
    return results.multi_face_landmarks[results_key]

In [35]:
def mediapipe_align(image, mp_results):
    left_iris = [474,475, 476, 477]
    right_iris = [469, 470, 471, 472]
    landmarks = [left_iris, right_iris]

    pixels = []
    for eye in landmarks:
        eye_pixels = []
        for num in eye:
            landmark = mp_results.landmark[num]
            coords = normal_to_pixel(float(landmark.x), float(landmark.y), image.shape[1], image.shape[0])
            eye_pixels.append(np.array(coords))
        pixels.append(np.array(eye_pixels))

    eye_centers = [(np.sum(eye, axis = 0) / len(eye)).astype(int) for eye in pixels]
    
    angle, direction = get_angle_from_eyes(eye_centers[0], eye_centers[1])

    rotated_image = rotate_from_angle(image, tuple(np.array(image.shape[1::-1]) / 2), angle, direction)
    
    return rotated_image

In [36]:
def get_mediapipe_region(image, mp_results):
    # Calculate the bounding box for the face based off of the minimum and maximum coordinates in found landmarks.
    # Landmarks are in normalized coordinates, so must be converted back to pixel coordinates.
    x_min = int(np.round(min([k.x for k in mp_results.landmark]) * image.shape[1]))
    x_max = int(np.round(max([k.x for k in mp_results.landmark]) * image.shape[1]))
    y_min = int(np.round(min([k.y for k in mp_results.landmark]) * image.shape[0]))
    y_max = int(np.round(max([k.y for k in mp_results.landmark]) * image.shape[0]))

    return x_min, x_max, y_min, y_max

In [51]:
def align_image(image, backend = ['dlib', 'retinaface', 'mediapipe']):
    
    if type(backend) == str:
        backend = [backend]
    
    for b in backend:
        if b == 'dlib':
            face_info = get_dlib_faces(image)
            if face_info == -1:
                continue
            rotated_image = dlib_align(image, face_info)
            
            return rotated_image
            
        if b == 'retinaface':
            face_info = get_retinaface_faces(image)
            if face_info == -1:
                continue
            rotated_image = retinaface_align(image, face_info)
            
            return rotated_image
        
        if b == 'mediapipe':
            face_info = get_mediapipe_faces(image)
            if face_info == -1:
                continue            
            rotated_image = mediapipe_align(image, face_info)
            
            return rotated_image
        
    return -1

In [52]:
def crop_image(image, backend = ['mediapipe', 'retinaface', 'dlib']):
    
    if type(backend) == str:
        backend = [backend]
    
    for b in backend:
        if b == 'mediapipe':
            face_info = get_mediapipe_faces(image)
            if face_info == -1:
                continue
            x_min, x_max, y_min, y_max = get_mediapipe_region(image, face_info)
            cropped_image = image[y_min:y_max, x_min:x_max, :]
            
            return cropped_image   
            
        if b == 'retinaface':
            face_info = get_retinaface_faces(image)
            if face_info == -1:
                continue            
            x_min, x_max, y_min, y_max = get_retinaface_region(face_info)
            cropped_image = image[y_min:y_max, x_min:x_max, :]
            
            return cropped_image   
        
        if b == 'dlib':
            face_info = get_dlib_faces(image)
            if face_info == -1:
                continue            
            x_min, x_max, y_min, y_max = get_dlib_region(face_info)
            cropped_image = image[y_min:y_max, x_min:x_max, :]
            
            return cropped_image
    
    return -1

In [17]:
def pad_image(image, end_dim = (250, 250), color = (0, 0, 0)):
    old_height, old_width, channels = image.shape
    new_height, new_width = end_dim
    
    x_center = (new_width - old_width) // 2
    y_center = (new_height - old_height) // 2
    
    y_top = y_center + old_height
    x_right = x_center + old_width
    
    padded_image = np.full((new_height, new_width, channels), color, dtype = np.uint8)
    
    padded_image[y_center:y_top, x_center:x_right] = image
    
    return padded_image

In [64]:
def preprocess_image(image, end_dim = (250, 250), color = (0, 0, 0),
                     alignment_backend =['dlib', 'retinaface', 'mediapipe'],
                     crop_backend = ['mediapipe', 'retinaface', 'dlib']):
    
    aligned_image = align_image(image, backend = alignment_backend)
    if type(aligned_image) == int and aligned_image == -1:
        if sorted(alignment_backend) == sorted(crop_backend):
            return -1
        else:
            aligned_image = image
    cropped_image = crop_image(aligned_image, backend = crop_backend)
    if type(cropped_image) == int and cropped_image == -1:
        return -1
    padded_image = pad_image(cropped_image, end_dim = end_dim, color = color)
    
    return padded_image

In [19]:
raw_path = './data/raw'
preprocessed_path = './data/preprocessed'
folder_names = ['train', 'test']

In [65]:
for folder in folder_names:
    image_names = os.listdir(os.path.join(raw_path, folder))
    for i, image_name in enumerate(image_names):
        print(f'Processing image {image_name}. {i + 1}/{len(image_names)}')
        image_path = os.path.join(raw_path, folder, image_name)
        dest_path = os.path.join(preprocessed_path, folder, image_name)
        
        if os.path.exists(dest_path):
            print(f'Image {image_name} already exists at {dest_path}.')
            continue
            
        image = cv2.imread(os.path.join(raw_path, folder, image_name))
        processed_image = preprocess_image(image)
        
        if type(processed_image) == int and processed_image == -1:
            print(f'Image {image_name} was not able to processed.')
            with open(os.path.join(raw_path, 'Bad_Images.txt'), 'w+') as f:
                f.write(f'{image_name},{folder}\n')
            continue
            
        cv2.imwrite(dest_path, processed_image)
        print(f'Image {image_name} successfully processed and written to {dest_path}.')

Processing image Aaron_Eckhart_0001.jpg. 1/9525
Image Aaron_Eckhart_0001.jpg already exists at ./data/preprocessed/train/Aaron_Eckhart_0001.jpg.
Processing image Aaron_Patterson_0001.jpg. 2/9525
Image Aaron_Patterson_0001.jpg already exists at ./data/preprocessed/train/Aaron_Patterson_0001.jpg.
Processing image Aaron_Peirsol_0001.jpg. 3/9525
Image Aaron_Peirsol_0001.jpg already exists at ./data/preprocessed/train/Aaron_Peirsol_0001.jpg.
Processing image Aaron_Peirsol_0002.jpg. 4/9525
Image Aaron_Peirsol_0002.jpg already exists at ./data/preprocessed/train/Aaron_Peirsol_0002.jpg.
Processing image Aaron_Peirsol_0003.jpg. 5/9525
Image Aaron_Peirsol_0003.jpg already exists at ./data/preprocessed/train/Aaron_Peirsol_0003.jpg.
Processing image Aaron_Peirsol_0004.jpg. 6/9525
Image Aaron_Peirsol_0004.jpg already exists at ./data/preprocessed/train/Aaron_Peirsol_0004.jpg.
Processing image Aaron_Pena_0001.jpg. 7/9525
Image Aaron_Pena_0001.jpg already exists at ./data/preprocessed/train/Aaron_Pen

Image Franz_Muentefering_0001.jpg already exists at ./data/preprocessed/train/Franz_Muentefering_0001.jpg.
Processing image Franz_Muentefering_0002.jpg. 2691/9525
Image Franz_Muentefering_0002.jpg already exists at ./data/preprocessed/train/Franz_Muentefering_0002.jpg.
Processing image Franz_Muentefering_0003.jpg. 2692/9525
Image Franz_Muentefering_0003.jpg already exists at ./data/preprocessed/train/Franz_Muentefering_0003.jpg.
Processing image Franz_Muentefering_0004.jpg. 2693/9525
Image Franz_Muentefering_0004.jpg already exists at ./data/preprocessed/train/Franz_Muentefering_0004.jpg.
Processing image Freda_Black_0001.jpg. 2694/9525
Image Freda_Black_0001.jpg already exists at ./data/preprocessed/train/Freda_Black_0001.jpg.
Processing image Freddy_Garcia_0001.jpg. 2695/9525
Image Freddy_Garcia_0001.jpg already exists at ./data/preprocessed/train/Freddy_Garcia_0001.jpg.
Processing image Freddy_Garcia_0002.jpg. 2696/9525
Image Freddy_Garcia_0002.jpg already exists at ./data/preproces

Image Juan_Roman_Carrasco_0001.jpg already exists at ./data/preprocessed/train/Juan_Roman_Carrasco_0001.jpg.
Processing image Juan_Valencia_Osorio_0001.jpg. 5192/9525
Image Juan_Valencia_Osorio_0001.jpg already exists at ./data/preprocessed/train/Juan_Valencia_Osorio_0001.jpg.
Processing image Juan_Valencia_Osorio_0002.jpg. 5193/9525
Image Juan_Valencia_Osorio_0002.jpg already exists at ./data/preprocessed/train/Juan_Valencia_Osorio_0002.jpg.
Processing image Judd_Davies_0001.jpg. 5194/9525
Image Judd_Davies_0001.jpg already exists at ./data/preprocessed/train/Judd_Davies_0001.jpg.
Processing image Judith_Nathan_0001.jpg. 5195/9525
Image Judith_Nathan_0001.jpg already exists at ./data/preprocessed/train/Judith_Nathan_0001.jpg.
Processing image Judy_Genshaft_0001.jpg. 5196/9525
Image Judy_Genshaft_0001.jpg already exists at ./data/preprocessed/train/Judy_Genshaft_0001.jpg.
Processing image Judy_Genshaft_0002.jpg. 5197/9525
Image Judy_Genshaft_0002.jpg already exists at ./data/preprocess

I0000 00:00:1720668475.344356   34427 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1720668475.348663   82293 gl_context.cc:357] GL version: 3.2 (OpenGL ES 3.2 Mesa 21.2.6), renderer: llvmpipe (LLVM 12.0.0, 256 bits)


Image Peter_Mugyeni_0001.jpg successfully processed and written to ./data/preprocessed/train/Peter_Mugyeni_0001.jpg.
Processing image Peter_Rasmussen_0001.jpg. 7337/9525


...

I0000 00:00:1720671131.264802   34427 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1720671131.267143  113152 gl_context.cc:357] GL version: 3.2 (OpenGL ES 3.2 Mesa 21.2.6), renderer: llvmpipe (LLVM 12.0.0, 256 bits)


Image Zoran_Djindjic_0004.jpg successfully processed and written to ./data/preprocessed/test/Zoran_Djindjic_0004.jpg.
Processing image Zulfiqar_Ahmed_0001.jpg. 3707/3708


I0000 00:00:1720671131.597720   34427 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1720671131.599372  113157 gl_context.cc:357] GL version: 3.2 (OpenGL ES 3.2 Mesa 21.2.6), renderer: llvmpipe (LLVM 12.0.0, 256 bits)


Image Zulfiqar_Ahmed_0001.jpg successfully processed and written to ./data/preprocessed/test/Zulfiqar_Ahmed_0001.jpg.
Processing image Zurab_Tsereteli_0001.jpg. 3708/3708
Image Zurab_Tsereteli_0001.jpg successfully processed and written to ./data/preprocessed/test/Zurab_Tsereteli_0001.jpg.


I0000 00:00:1720671131.947229   34427 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1720671131.948945  113162 gl_context.cc:357] GL version: 3.2 (OpenGL ES 3.2 Mesa 21.2.6), renderer: llvmpipe (LLVM 12.0.0, 256 bits)
